In [ ]:
%matplotlib inline
import pandas as pd
import numpy as np
import pylab as plt
import matplotlib.ticker as mtick
import seaborn as sns
from scipy.interpolate import griddata

# hide warnings
import warnings
warnings.filterwarnings('ignore')

# default font size
plt.rcParams.update({'font.size':'14'})

# sectors
secsel = ['Industry','Transportation','Residential and Commercial']
sect_palette = [sns.color_palette('pastel')[7], # industry
                sns.color_palette('tab10')[1],  # transport
                sns.color_palette('tab10')[0]]  # buildings

# models
models_order = {
    'IMAGE 3.2': 1,
    'MESSAGEix-GLOBIOM 1.2': 2,
    'PRIMES 2022': 3,
    'PROMETHEUS 1.2': 4,
    'REMIND 2.1': 5,
    'TIAM-ECN 1.2': 6,
    'WITCH 5.1': 7,
    'Euro-Calliope 2.0': 8
}

# scenarios
scensel = ['DIAG-NPI','DIAG-C0to80-gr5','DIAG-C400-lin']
scen_names = {'DIAG-NPI':'1. NPI',
              'DIAG-C0to80-gr5': '2. C0-80',
              'DIAG-C400-lin':'3. C400-lin',
             }

# energy carriers
carriers = ['Electricity','Gases','Heat','Hydrogen','Liquids','Solids','Other']

# years
yearsel = [2020,2030,2040,2050]

# input data
data = pd.read_excel("ECEMF_T3.1_Data.xlsx").drop(['version','Work package'], axis=1)
data.head()

# Figure 1

In [ ]:
df = data[(data.variable=='Emissions|CO2') &\
          (data.year.isin(yearsel))][['model','scenario','year','value']]\
     .groupby(['scenario','year']).agg(['mean','std']).reset_index()
df.columns = ['scenario','year','co2', 'co2_std']
df['scenario'] = df['scenario'].map(scen_names)
df.sort_values(by=['scenario','year'], inplace=True)

sns.lineplot(data=df,x='year',y='co2',hue='scenario',marker='o')

for s in scensel: 
    dfs = df[df['scenario']==scen_names[s]]
    plt.fill_between(dfs['year'],dfs['co2']-dfs['co2_std'],dfs['co2']+dfs['co2_std'],alpha=0.3)

plt.ylabel(r'CO$_2$ emissions [Mt/yr]')
plt.gca().legend(['NPI','C0-80','C400-lin'], frameon=False, loc='lower left')
plt.title('CO$_2$ emissions')
plt.tight_layout()

# Figure 2
## Electricity

In [ ]:
df = data[(data['variable'].str.startswith('Secondary Energy|Electricity')) &\
          (data.year.isin(yearsel))]
df[['vartype','carrier','tech','ccs']] = df['variable'].str.split('|',expand=True)
techsel = ['Fossil', 'Biomass','Hydro', 'Solar','Wind', 'Nuclear', 'Hydrogen']
df = df[(df.tech.isin(techsel)) & (df.ccs.isnull())][['model','scenario','tech','year','value']]

fig, ax = plt.subplots(1,3,sharex=True,sharey=True)
fig.set_size_inches(12,4)

for i in range(len(scensel)):
    sns.barplot(data=df[df.scenario==scensel[i]],\
              x='tech',y='value',hue='year',ax=ax[i],errwidth=0.5,palette='viridis')
    
    # get xtick labels and shift down the odd ones for readability
    xtix = ax[i].get_xticklabels()
    for j,t in enumerate(xtix):
        if j/2.!=j//2:
            t.set_y(t.get_position()[1]-0.1)
    
    ax[i].set_xlabel('')
    ax[i].set_ylim(0,16)
    ax[i].set_title(scen_names[scensel[i]][3:])
    ax[i].legend([],[],frameon=False)
    ax[i].set_ylabel('')

ax[0].legend(ax[i].get_legend_handles_labels()[0],yearsel,frameon=False)
ax[0].set_ylabel('Electricity production [EJ/yr]')
fig.suptitle('Electricity')

plt.tight_layout()



## H2

In [ ]:
df = data[(data['variable'].str.startswith('Secondary Energy|Hydrogen')) &\
          (data.year.isin(yearsel))]
df[['vartype','carrier','tech','ccs']] = df['variable'].str.split('|',expand=True)
techsel = ['Fossil', 'Biomass','Electricity']
df = df[(df.tech.isin(techsel)) & (df.ccs.isnull())][['model','scenario','tech','year','value']]

df.head()

fig, ax = plt.subplots(1,3,sharey=True)
fig.set_size_inches(12,4)

for i in range(len(scensel)):
    sns.barplot(data=df[df.scenario==scensel[i]],\
            hue='year',y='value',x='tech',ax=ax[i],errwidth=0.5,palette='viridis')
    
    ax[i].set_ylim(0,4)
    ax[i].set_title(scen_names[scensel[i]][3:])
    ax[i].legend([],[],frameon=False)
    ax[i].set_ylabel('')
    ax[i].set_xlabel('')

ax[0].legend(ax[i].get_legend_handles_labels()[0],yearsel,frameon=False)
ax[0].set_ylabel(r'H$_2$ production [EJ/yr]')
fig.suptitle('H$_2$')

plt.tight_layout()


# Figure 3

In [ ]:
varsel = [v for v in data.variable.unique() if v.startswith(f'Final Energy|Industry')] +\
         [v for v in data.variable.unique() if v.startswith(f'Final Energy|Transportation')] +\
         [v for v in data.variable.unique() if v.startswith(f'Final Energy|Residential and Commercial')]

df = data[(data.variable.isin(varsel)) &\
          (data.year.isin(yearsel))][['model','scenario','variable','year','value']]

carriers = ['Electricity','Gases','Heat','Hydrogen','Liquids','Solids','Other']


for sec in secsel:
    print(sec)
    fig, ax = plt.subplots(1,3,sharex=True,sharey=True)
    fig.set_size_inches(12,4)
    for i in range(len(scensel)):
        s = scensel[i]
        varlist = [f'Final Energy|{sec}|{c}' for c in carriers]
        df_toplot = df[df.variable.isin(varlist)].replace(dict(zip(varlist,carriers)))
        sortvar = df_toplot['variable'].replace({'Other':'zOther'})
        sortvar.sort_values()
        df_toplot['order'] = sortvar
        df_toplot.sort_values('order',inplace=True)
        
        sns.barplot(data=df_toplot[df_toplot['scenario']==s],\
                  hue='year',y='value',x='variable',ax=ax[i],errwidth=0.5,palette='viridis')

        # get xtick labels and shift down the odd ones for readability
        xtix = ax[i].get_xticklabels()
        for j,t in enumerate(xtix):
            if j/2.!=j//2:
                t.set_y(t.get_position()[1]-0.1)

        ax[i].set_xlabel('')
        ax[i].set_ylim(0,15)
        ax[i].set_title(scen_names[scensel[i]][3:])
        ax[i].legend([],[],frameon=False)
        ax[i].set_ylabel('')
    ax[0].legend(ax[i].get_legend_handles_labels()[0],yearsel,frameon=False)
    if sec == 'Residential and Commercial':
        ax[0].set_ylabel(f'Buildings mix [EJ/yr]')
        fig.suptitle(f'Buildings')
    else: 
        ax[0].set_ylabel(f'{sec} mix [EJ/yr]')
        fig.suptitle(f'{sec}')
    plt.tight_layout()


# Figure 4

In [ ]:
varsel = ['Final Energy','Final Energy|Electricity','Final Energy|Hydrogen','Emissions|CO2']
df = data[(data.variable.isin(varsel)) &\
          (data.year.isin(yearsel))][['model','scenario','variable','year','value']]


# calculate electricity and hydrogen shares in FEC

fe = df[df.variable=='Final Energy'].pivot(index=['model','scenario'],
                                           columns=['year'],
                                           values=['value'])
elc = df[df.variable=='Final Energy|Electricity'].pivot(index=['model','scenario'],
                                                        columns=['year'],
                                                        values=['value'])
h2 =  df[df.variable=='Final Energy|Hydrogen'].pivot(index=['model','scenario'],
                                                     columns=['year'],
                                                     values=['value'])

elc_share = (elc/fe).reset_index()
elc_share.columns = ['model','scenario'] + yearsel
elc_share = elc_share.melt(id_vars=['model','scenario'],
                           value_vars=yearsel, var_name='year')
elc_share['variable'] = 'Electricity share'
elc_share = elc_share[df.columns]

h2_share = (h2/fe).reset_index()
h2_share.columns = ['model','scenario'] + yearsel
h2_share = h2_share.melt(id_vars=['model','scenario'],
                         value_vars=yearsel, var_name='year')

h2_share['variable'] = 'Hydrogen share'
h2_share = h2_share[df.columns]

df = pd.concat([df,elc_share,h2_share],ignore_index=True)

df_toplot = df.groupby(['scenario','year','variable']).agg(['mean','std']).reset_index()
df_toplot.columns = ['scenario','year','variable','mean','std']
df_toplot = df_toplot[df_toplot.variable.isin(['Emissions|CO2','Electricity share','Hydrogen share'])]
df_toplot = df_toplot.pivot(index=['scenario','year'],
                            columns=['variable'],
                            values=['mean','std']).reset_index()
df_toplot.columns = ['scenario','year','elc','co2','h2',
                     'elc_std','co2_std','h2_std']
df_toplot['scenario'] = df_toplot['scenario'].map(scen_names)
df_toplot = df_toplot.sort_values(by='scenario')


## Electricity

In [ ]:
sns.lineplot(data=df_toplot,x='year',y='elc',hue='scenario',marker='o')
for s in scensel: 
    dfs = df_toplot[df_toplot['scenario']==scen_names[s]]
    plt.fill_between(dfs['year'],dfs['elc']-dfs['elc_std'],dfs['elc']+dfs['elc_std'],alpha=0.3)

plt.gca().yaxis.set_major_formatter(mtick.PercentFormatter(1,0))
plt.ylabel(r'Electricity share in FEC')
plt.gca().legend(['NPI','C0-80','C400-lin'], frameon=False, loc='upper left')
plt.title('Electricity share')

plt.tight_layout()

## H2

In [ ]:
sns.lineplot(data=df_toplot,x='year',y='h2',hue='scenario',marker='o')
for s in scensel: 
    dfs = df_toplot[df_toplot['scenario']==scen_names[s]]
    plt.fill_between(dfs['year'],dfs['h2']-dfs['h2_std'],dfs['h2']+dfs['h2_std'],alpha=0.3)

plt.gca().yaxis.set_major_formatter(mtick.PercentFormatter(1,0))
plt.ylabel(r'H$_2$ share in FEC')
plt.gca().legend(['NPI','C0-80','C400-lin'], loc='upper left', frameon=False)
plt.title('H$_2$ share')

plt.tight_layout()

# Figure 6
## Electricity

In [ ]:
sns.lineplot(data=df_toplot,x='elc',y='co2',hue='scenario',marker='o')
for s in scensel: 
    dfs = df_toplot[df_toplot['scenario']==scen_names[s]]
    plt.fill_between(dfs['elc'],dfs['co2']-dfs['co2_std'],dfs['co2']+dfs['co2_std'],alpha=0.3)

plt.gca().xaxis.set_major_formatter(mtick.PercentFormatter(1,0))
plt.ylabel(r'CO$_2$ emissions [Mt/yr]')
plt.xlabel(r'Electricity share in FEC')
plt.gca().legend(['NPI','C0-80','C400-lin'], frameon=False, loc='lower left', title=None)
plt.title('CO$_2$ vs electricity share')

plt.tight_layout()


## H2

In [ ]:
sns.lineplot(data=df_toplot,x='h2',y='co2',hue='scenario',marker='o')
for s in scensel: 
    dfs = df_toplot[df_toplot['scenario']==scen_names[s]]
    plt.fill_between(dfs['h2'],dfs['co2']-dfs['co2_std'],dfs['co2']+dfs['co2_std'],alpha=0.3)

plt.gca().xaxis.set_major_formatter(mtick.PercentFormatter(1,0))
plt.ylabel(r'CO$_2$ emissions [Mt/yr]')
plt.xlabel(r'H$_2$ share in FEC')
plt.gca().legend(['NPI','C0-80','C400-lin'], frameon=False, title=None)
plt.title('CO$_2$ vs H$_2$ share')

plt.tight_layout()

# Figure 9

In [ ]:
df_plt = df[(df.variable.isin(['Emissions|CO2','Electricity share', 'Hydrogen share'])) &\
            (df.year==2050) &\
            (~df.model.str.contains('Euro-Calliope')) &\
            (~df.model.str.contains('WITCH')) 
           ].dropna()
df_plt = df_plt.pivot(index=['model','scenario','year'],
                      columns='variable',
                      values='value').reset_index().dropna()
df_plt.columns = ['model','scenario','year','elc','co2','h2']
df_plt['scenario'] = df_plt['scenario'].map(scen_names)

# smaller fonts
plt.rcParams.update({'font.size':'12'})

x = df_plt.h2
y = df_plt.elc
z = df_plt.co2
levels = np.arange(-1000,3500,50)


def plot_contour(x,y,z,resolution = 50,contour_method='linear'):
    resolution = str(resolution)+'j'
    X,Y = np.mgrid[min(x):max(x):complex(resolution),   min(y):max(y):complex(resolution)]
    points = [[a,b] for a,b in zip(x,y)]
    Z = griddata(points, z, (X, Y), method=contour_method)
    return X,Y,Z

X,Y,Z = plot_contour(x,y,z,resolution = 500,contour_method='linear')


fig, ax = plt.subplots(figsize=(12,8))
cs = ax.contourf(X,Y,Z,cmap='terrain',levels=levels)

# ax.scatter(x,y,c=z, linewidth=1, edgecolor="ivory", s=50)
# sns.lineplot(data=df_plt,x='h2',y='elc',hue='scenario',marker='o',linewidth=0,palette=['Black','Dimgrey','Silver','Whitesmoke']\
#              ,markeredgecolor='black' #,palette='Reds',legend=False
#             )
sns.scatterplot(data=df_plt,x='h2',y='elc',hue='model',style='scenario',s=250,
                style_order=['1. NPI','2. C0-80','3. C400-lin'])

plt.xlim(-0.005,0.145)
plt.ylim(0.2,0.65)
plt.gca().xaxis.set_major_formatter(mtick.PercentFormatter(1,0))
plt.gca().yaxis.set_major_formatter(mtick.PercentFormatter(1,0))

plt.xlabel(r'H$_2$ share in FEC')
plt.ylabel(r'Electricity share in FEC')

plt.colorbar(cs,label=r'CO$_2$ emissions [Mt/yr]')
leg = plt.legend(bbox_to_anchor=[2.,1], frameon=False)
for t in leg.get_texts():
    if t.get_text()=='1. NPI':
        t.set_text('NPI')
    if t.get_text()=='2. C0-80':
        t.set_text('C0-80')
    if t.get_text()=='3. C400-lin':
        t.set_text('C400-lin')
plt.title('Electricity share vs H$_2$ share')

plt.tight_layout()


In [ ]:
# restore bigger fonts
plt.rcParams.update({'font.size':'14'})

# Figure 11

In [ ]:
df_plt = df[(df.variable.isin(['Emissions|CO2','Electricity share', 'Hydrogen share']))]
df_plt = df_plt.pivot(index=['model','scenario','year'],
                      columns='variable',
                      values='value').reset_index().dropna()
df_plt.columns = ['model','scenario','year','elc','co2','h2']
df_plt['scenario'] = df_plt['scenario'].map(scen_names)
df_plt['model_ord'] = df_plt['model'].map(models_order)
df_plt = df_plt.sort_values('model_ord')


## Electricity

In [ ]:
fig, ax = plt.subplots(1,3,sharey=True, sharex=True)
fig.set_size_inches(12,3)
for i in range(len(scensel)):
    sns.lineplot(data=df_plt[df_plt['scenario']==scen_names[scensel[i]]].sort_values('model_ord'),\
                 x='elc',y='co2',\
                 hue='model',hue_order=df_plt['model'].unique(),marker='o',ax=ax[i])
 
    ax[i].set_title(scen_names[scensel[i]][3:])
    ax[i].legend([],[],frameon=False)
    ax[i].set_ylabel('')
    ax[i].xaxis.set_major_formatter(mtick.PercentFormatter(1,0))
    ax[i].set_xlabel(r'Electricity share in FEC')
    
ax[0].set_ylabel(r'CO$_2$ emissions [Mt/yr]')
ax[2].legend(ax[i].get_legend_handles_labels()[0],df.model.unique())
ax[2].legend(bbox_to_anchor=[1,1], frameon=False)

fig.suptitle('Electricity')

plt.tight_layout()

## H2

In [ ]:
fig, ax = plt.subplots(1,3,sharey=True, sharex=True)
fig.set_size_inches(12,3)
for i in range(len(scensel)):
    sns.lineplot(data=df_plt[df_plt['scenario']==scen_names[scensel[i]]],x='h2',y='co2',\
                 hue='model',hue_order=df_plt['model'].unique(),marker='o',ax=ax[i])
 
    ax[i].set_title(scen_names[scensel[i]][3:])
    ax[i].legend([],[],frameon=False)
    ax[i].set_ylabel('')
    ax[i].xaxis.set_major_formatter(mtick.PercentFormatter(1,0))
    ax[i].set_xlabel(r'H$_2$ share in FEC')
    
ax[0].set_ylabel(r'CO$_2$ emissions [Mt/yr]')
ax[2].legend(ax[i].get_legend_handles_labels()[0],df.model.unique())
ax[2].legend(bbox_to_anchor=[1,1], frameon=False)

fig.suptitle('H$_2$')

plt.tight_layout()

# Figure 5

In [ ]:
varsel = [f'Final Energy|{s}' for s in secsel] +\
         [f'Final Energy|{s}|Electricity' for s in secsel] +\
         [f'Final Energy|{s}|Hydrogen' for s in secsel] +\
         [f'Emissions|CO2|Energy|Demand|{s}' for s in secsel] 
df57 = data[(data.variable.isin(varsel)) &\
            (data.year.isin(yearsel))][['model','scenario','variable','year','value']]
df = df57.copy()
# calculate electricity and hydrogen shares in FEC per sector
dfs = []
for s in secsel:
    fe = df[df.variable==f'Final Energy|{s}'].pivot(index=['model','scenario'],
                                                    columns=['year'],
                                                    values=['value'])
    elc = df[df.variable==f'Final Energy|{s}|Electricity'].pivot(index=['model','scenario'],
                                                                 columns=['year'],
                                                                 values=['value'])
    h2 =  df[df.variable==f'Final Energy|{s}|Hydrogen'].pivot(index=['model','scenario'],
                                                             columns=['year'],
                                                             values=['value'])

    elc_share = (elc/fe).reset_index()
    elc_share.columns = ['model','scenario'] + yearsel
    elc_share = elc_share.melt(id_vars=['model','scenario'],
                               value_vars=yearsel, var_name='year')
    elc_share['variable'] = f'{s}|Electricity share'
    elc_share = elc_share[df.columns]

    h2_share = (h2/fe).reset_index()
    h2_share.columns = ['model','scenario'] + yearsel
    h2_share = h2_share.melt(id_vars=['model','scenario'],
                             value_vars=yearsel, var_name='year')

    h2_share['variable'] = f'{s}|Hydrogen share'
    h2_share = h2_share[df.columns]
    dfs.append(pd.concat([elc_share,h2_share],ignore_index=True))

df = pd.concat(dfs)
df['scenario'] = df['scenario'].map(scen_names)


## Electricity

In [ ]:
fig, ax = plt.subplots(1,3,sharey=True)
fig.set_size_inches(12, 4)

for i in range(len(scensel)):
    sns.boxplot(data=df[(df.scenario==scen_names[scensel[i]]) &\
                        (df.variable.str.contains('Electricity share'))],\
                x='year',y='value',hue='variable',ax=ax[i],palette=sect_palette,fliersize=0)
    ax[i].set_ylim(0,1.)
    ax[i].set_title(scen_names[scensel[i]][3:])
    ax[i].legend([],[],frameon=False)
    ax[i].set_ylabel('')
    
ax[0].legend(ax[i].get_legend_handles_labels()[0],['Industry','Transportation','Buildings'], frameon=False)
ax[0].yaxis.set_major_formatter(mtick.PercentFormatter(1,0))
ax[0].set_ylabel('Electricity share in FEC')
fig.suptitle('Electricity')

plt.tight_layout()

## H2

In [ ]:
fig, ax = plt.subplots(1,3,sharey=True)
fig.set_size_inches(12,4)
for i in range(len(scensel)):
    sns.boxplot(data=df[(df.scenario==scen_names[scensel[i]]) &\
                        (df.variable.str.contains('Hydrogen share'))],\
                x='year',y='value',hue='variable',ax=ax[i],palette=sect_palette,fliersize=0)
    ax[i].set_ylim(0,0.3)
    ax[i].set_title(scen_names[scensel[i]][3:])
    ax[i].legend([],[],frameon=False)
    ax[i].set_ylabel('')
    
ax[0].yaxis.set_major_formatter(mtick.PercentFormatter(1,0))
ax[0].legend(ax[i].get_legend_handles_labels()[0],['Industry','Transportation','Buildings'],frameon=False)
ax[0].set_ylabel(r'H$_2$ share in FEC')
fig.suptitle('H$_2$')

plt.tight_layout()

# Figure 7

In [ ]:
df57['scenario'] = df57['scenario'].map(scen_names)
for s in secsel:
    df57 = df57.replace(f'Emissions|CO2|Energy|Demand|{s}',f'{s}|co2')
df = pd.concat([df,df57[df57.variable.str.contains('co2')]], ignore_index=True)
df[['sector','var']] = df['variable'].str.split('|', expand=True)
df = df.pivot(index=['model','scenario','year','sector'], columns='var',values='value').reset_index()
df.columns = ['model','scenario','year','sector','elc','h2','co2']

# exclude EuroCallope and WITCH beacuse of too many nans
df = df[(~df.model.str.contains('Calliope')) & (~df.model.str.contains('WITCH'))]


## Electricity

In [ ]:
# df = pd.read_excel(data_file, sheet_name="Fig7&8")

df3 = df.groupby(['scenario','year','sector']).aggregate(['mean','std']).reset_index()
df3.columns = ['scenario','year','sector','elc_share','elc_std','h2_share','h2_std','co2','co2_std']

fig, ax = plt.subplots(1,3,sharey=True,sharex=True)
fig.set_size_inches(12,4)
for i in range(len(secsel)):
    df1 = df3[df3.sector==secsel[i]].groupby(['scenario','year','sector']).aggregate('mean')
    sns.lineplot(data=df1,x='elc_share',y='co2',hue='scenario',ax=ax[i],marker='o')
    for s in scensel: 
        dfs = df3[(df3['scenario']==scen_names[s]) & (df3['sector']==secsel[i])]
        ax[i].fill_between(dfs['elc_share'],dfs['co2']-dfs['co2_std'],dfs['co2']+dfs['co2_std'],alpha=0.3)

    plt.fill_between
    ax[i].xaxis.set_major_formatter(mtick.PercentFormatter(1,0))
    ax[i].legend([],[],frameon=False)
    ax[i].set_xlabel('')
ax[0].set_title('Industry')
ax[1].set_title('Transportation')
ax[2].set_title('Buildings')
fig.suptitle('Sectoral CO$_2$ emissions vs electricity share')

ax[0].legend(ax[2].get_legend_handles_labels()[0],['NPI','C0-80','C400-lin'],frameon=False,loc='upper left')
# plt.xlabel('Electricity and hydrogen share of FEC [-]')
fig.supxlabel('Electricity share of sectoral FEC', fontsize=14)
ax[0].set_ylabel(r'CO$_2$ emissions [Mt/yr]')

plt.tight_layout()

## H2

In [ ]:
fig, ax = plt.subplots(1,3,sharey=True,sharex=True)
fig.set_size_inches(12,4)

for i in range(len(secsel)):
    df1 = df3[df3.sector==secsel[i]].groupby(['scenario','year','sector']).aggregate('mean')
    sns.lineplot(data=df1,x='h2_share',y='co2',hue='scenario',ax=ax[i],marker='o')
    for s in scensel: 
        dfs = df3[(df3['scenario']==scen_names[s]) & (df3['sector']==secsel[i])]
        ax[i].fill_between(dfs['h2_share'],dfs['co2']-dfs['co2_std'],dfs['co2']+dfs['co2_std'],alpha=0.3)

    plt.fill_between
    ax[i].legend([],[],frameon=False)
    ax[i].xaxis.set_major_formatter(mtick.PercentFormatter(1,1))
    ax[i].set_xlabel('')
ax[0].set_title('Industry')
ax[1].set_title('Transportation')
ax[2].set_title('Buildings')

ax[0].legend(ax[i].get_legend_handles_labels()[0],[scen_names[s] for s in scensel])
# plt.xlabel('Electricity and hydrogen share of FEC [-]')
ax[0].set_ylabel(r'Sectoral CO$_2$ emissions [Mt/yr]')

fig.suptitle('Sectoral CO$_2$ emissions vs H$_2$ share')

ax[0].legend(ax[2].get_legend_handles_labels()[0],['NPI','C0-80','C400-lin'],frameon=False,loc='upper left')
# plt.xlabel('Electricity and hydrogen share of FEC [-]')
fig.supxlabel('H$_2$ share of sectoral FEC', fontsize=14)
ax[0].set_ylabel(r'CO$_2$ emissions [Mt/yr]')

plt.tight_layout()

# Figure 8

In [ ]:
fig,ax = plt.subplots(1,2,sharey=True,sharex=True)
fig.set_size_inches(12,4.5)
carrs = ['elc','h2']

for i in range(len(carrs)):
    c = carrs[i]
    a = ax[i]
    sns.scatterplot(data=df.sort_values(by=['scenario','model']),x=f'{c}',y='co2',\
                hue='model',style='scenario',s=100,ax=a)
    sns.regplot(data=df.sort_values(by=['scenario','model']),x=f'{c}',y='co2',\
                scatter=False,color='k',ax=a)
    a.set_ylim(-250,1250)
    a.xaxis.set_major_formatter(mtick.PercentFormatter(1,0))
    
ax[0].legend([],[],frameon=False)
ax[0].set_xlabel('Electriticy share in FEC')
ax[0].set_ylabel(r'CO$_2$ emissions [Mt/yr]')
ax[0].set_title('CO$_2$ vs electricity share')

ax[1].set_xlabel(r'H$_2$ share in FEC')
ax[1].set_title('CO$_2$ vs H$_2$ share')
leg = ax[1].legend(frameon=False, fontsize=10)
for t in leg.get_texts():
    if t.get_text()=='1. NPI':
        t.set_text('NPI')
    if t.get_text()=='2. C0-80':
        t.set_text('C0-80')
    if t.get_text()=='3. C400-lin':
        t.set_text('C400-lin')

plt.tight_layout()

# Figure 12
## Electricity

In [ ]:
df.head()

In [ ]:
# df = pd.read_excel(data_file, sheet_name="Fig7&8")

df['model_ord'] = df['model'].map(models_order)
# df = df.sort_values(by=['model_ord'])

fig,ax = plt.subplots(1,3,sharey=True)
fig.set_size_inches(12,4)
fig.suptitle('Sectoral CO$_2$ emissions vs electricity share')
# elc
for i in range(len(secsel)):
    s = secsel[i]
    a = ax[i]
    sns.scatterplot(data=df[df['sector']==s].sort_values(by=['scenario','model_ord']),\
                    x='elc',y='co2',hue='model',style='scenario',s=100,ax=a)
    sns.regplot(data=df[df['sector']==s].sort_values(by=['scenario','model_ord']),\
                x='elc',y='co2',scatter=False,color='k',ax=a)
    a.set_ylim(-250,1250)
    a.set_title(f'{s}')
    a.set_xlim(-0.05,0.9)
    a.xaxis.set_major_formatter(mtick.PercentFormatter(1,0))
    a.set_xlabel('Electricity share in FEC')
    a.legend([],[],frameon=False)
ax[0].set_ylabel('CO$_2$ emissions [Mt/yr]')
    
plt.tight_layout()

## H2

In [ ]:
fig,ax = plt.subplots(1,3,sharey=True)
fig.set_size_inches(12,4)
fig.suptitle('Sectoral CO$_2$ emissions vs H$_2$ share')

#h2
for i in range(len(secsel)):
    s = secsel[i]
    a = ax[i]
    sns.scatterplot(data=df[df['sector']==s].sort_values(by=['scenario','model_ord']),\
                    x='h2',y='co2',hue='model',style='scenario',s=100,ax=a)
    sns.regplot(data=df[df['sector']==s].sort_values(by=['scenario','model_ord']),\
                x='h2',y='co2',scatter=False,color='k',ax=a)
    a.set_ylim(-250,1250)
    a.set_xlim(-0.05,0.9)
    a.xaxis.set_major_formatter(mtick.PercentFormatter(1,0))
    a.set_title(s)
    a.set_xlabel('H$_2$ share in FEC')
    a.legend([],[],frameon=False)

ax[0].set_ylabel('CO$_2$ emissions [Mt/yr]')
ax[2].set_title('Buildings')    
leg = ax[2].legend(fontsize=9,frameon=False)
for t in leg.get_texts():
    if t.get_text()=='1. NPI':
        t.set_text('NPI')
    if t.get_text()=='2. C0-80':
        t.set_text('C0-80')
    if t.get_text()=='3. C400-lin':
        t.set_text('C400-lin')

plt.tight_layout()

# Figure 10

In [ ]:
varsel = ['Trade|Secondary Energy|Electricity|Volume','Trade|Secondary Energy|Hydrogen|Volume',\
          'Secondary Energy|Electricity','Secondary Energy|Hydrogen',\
          'Final Energy|Electricity','Final Energy|Hydrogen']
df = data[(data.variable.isin(varsel)) &\
          (data.year.isin(yearsel))][['model','scenario','variable','year','value']]
df.head()

In [ ]:
df_toplot = df.copy()
df_toplot.columns = list(df.columns)[:-1] + ['val']

for c in ['Electricity','Hydrogen']:
    idx = df_toplot.groupby(['model','scenario','year']).agg(sum).index
    step1 = pd.DataFrame(index=idx,columns=['variable']).fillna(0)
    step1.columns = ['val']

    trade = df_toplot[df_toplot['variable']==f'Trade|Secondary Energy|{c}|Volume']\
                .set_index(['model','scenario','year'])\
                .drop('variable',axis=1)

    step1.loc[trade.index,'val'] = df_toplot[df_toplot['variable']==f'Trade|Secondary Energy|{c}|Volume']\
             .set_index(['model','scenario','year'])\
             .drop('variable',axis=1).loc[trade.index,'val']

    step2 = step1.reset_index()
    step2['variable'] = f'Trade|Secondary Energy|{c}|Volume'

    idx_todrop = df_toplot[df_toplot['variable']==f'Trade|Secondary Energy|{c}|Volume'].index
    df_toplot.drop(idx_todrop,axis=0,inplace=True)
    df_toplot = pd.concat([df_toplot,step2]).reset_index(drop=True)

# net supply
for c in ['Electricity','Hydrogen']:
    step1 = df_toplot.set_index(['model','scenario','year'])
    step2 = pd.DataFrame(step1[step1.variable==f'Secondary Energy|{c}']['val'] -\
               step1[step1.variable==f'Trade|Secondary Energy|{c}|Volume']['val']).fillna(0)
    step2['variable'] = f'Total Supply|{c}'
    df_toplot = pd.concat([df_toplot,step2.reset_index()]).reset_index(drop=True)

elc_s = df_toplot[df_toplot['variable']=='Total Supply|Electricity'].groupby(['model','scenario','year']).agg('sum').reset_index()
elc_s.columns = ['model','scenario','year','elc_s']
elc_u = df_toplot[df_toplot['variable']=='Final Energy|Electricity'].groupby(['model','scenario','year']).agg('sum').reset_index()
elc_u.columns = ['model','scenario','year','elc_u']
elc = elc_s.merge(elc_u, on=['model','scenario','year'], how='left')
elc = elc.replace(scen_names).sort_values('scenario')


h2_s = df_toplot[df_toplot['variable']=='Total Supply|Hydrogen'].groupby(['model','scenario','year']).agg('sum').reset_index()
h2_s.columns = ['model','scenario','year','h2_s']
h2_u = df_toplot[df_toplot['variable']=='Final Energy|Hydrogen'].groupby(['model','scenario','year']).agg('sum').reset_index()
h2_u.columns = ['model','scenario','year','h2_u']
h2 = h2_s.merge(h2_u, on=['model','scenario','year'], how='left')
h2 = h2.replace(scen_names).sort_values('scenario')

elc['model_ord'] = elc['model'].map(models_order)
idx = elc[elc.model_ord.isnull()].index
elc.loc[idx,'model_ord'] = elc.loc[idx,'model']

h2['model_ord'] = h2['model'].map(models_order)
idx = h2[h2.model_ord.isnull()].index
h2.loc[idx,'model_ord'] = h2.loc[idx,'model']



## Electricity

In [ ]:
ax = sns.lineplot(data=elc[elc.scenario=='3. C400-lin'].sort_values(by='model_ord'),x='elc_s',y='elc_u',hue='model',\
                  marker='o',legend=False)
plt.plot(range(0,40,1),range(0,40,1),'--',color='k')
plt.xlabel(r'Total Electricity supply [EJ/yr]')
plt.ylabel(r'Total Electricity in FEC [EJ/yr]')
plt.xlim(0,40)
plt.ylim(0,40)
plt.title('Electricity use vs supply')

## H2

In [ ]:
ax = sns.lineplot(data=h2[h2.scenario=='3. C400-lin'].sort_values(by='model_ord'),x='h2_s',y='h2_u',hue='model',\
             marker='o')
plt.plot(range(0,13,1),range(0,13,1),'--',color='k')
plt.xlabel(r'Total H$_2$ supply [EJ/yr]')
plt.ylabel(r'Total H$_2$ in FEC [EJ/yr]')
plt.xlim(-0.5,18.5)
plt.ylim(-0.5,18.5)
plt.gca().legend(ncol=2, loc='upper center',frameon=False, fontsize=12)
plt.title('H$_2$ use vs supply')
